Basic informations about dataset:
The data contains information from the 1990 California census. So although it may not help you with predicting current housing prices like the Zillow Zestimate dataset, it does provide an accessible introductory dataset for teaching people about the basics of machine learning.


Size:
* number of features (columns): 10
* number of rows: 20640

## 1. DATA PREPROCESSING

### 1.1 IMPORTING MODULES

In [1]:
import pandas as pd
import numpy as np

import matplotlib.pyplot as plt
import matplotlib
import seaborn as sns
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.simplefilter(action='ignore', category=UserWarning)
sns.set(style="white")

import plotly
import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.figure_factory as ff

from plotly.offline import plot, iplot, init_notebook_mode
init_notebook_mode(connected=True)


from sklearn.neighbors import KNeighborsRegressor
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score

df = pd.read_csv('../input/california-housing-prices/housing.csv')

In [2]:
df.head() #  showing first 5 rows

longitude  latitude  housing_median_age  total_rooms  total_bedrooms  \
0    -122.23     37.88                41.0        880.0           129.0   
1    -122.22     37.86                21.0       7099.0          1106.0   
2    -122.24     37.85                52.0       1467.0           190.0   
3    -122.25     37.85                52.0       1274.0           235.0   
4    -122.25     37.85                52.0       1627.0           280.0   

   population  households  median_income  median_house_value ocean_proximity  
0       322.0       126.0         8.3252            452600.0        NEAR BAY  
1      2401.0      1138.0         8.3014            358500.0        NEAR BAY  
2       496.0       177.0         7.2574            352100.0        NEAR BAY  
3       558.0       219.0         5.6431            341300.0        NEAR BAY  
4       565.0       259.0         3.8462            342200.0        NEAR BAY

In [3]:
df.describe() #  inspecting numerical features

longitude      latitude  housing_median_age   total_rooms  \
count  20640.000000  20640.000000        20640.000000  20640.000000   
mean    -119.569704     35.631861           28.639486   2635.763081   
std        2.003532      2.135952           12.585558   2181.615252   
min     -124.350000     32.540000            1.000000      2.000000   
25%     -121.800000     33.930000           18.000000   1447.750000   
50%     -118.490000     34.260000           29.000000   2127.000000   
75%     -118.010000     37.710000           37.000000   3148.000000   
max     -114.310000     41.950000           52.000000  39320.000000   

       total_bedrooms    population    households  median_income  \
count    20433.000000  20640.000000  20640.000000   20640.000000   
mean       537.870553   1425.476744    499.539680       3.870671   
std        421.385070   1132.462122    382.329753       1.899822   
min          1.000000      3.000000      1.000000       0.499900   
25%        296.000000    787.000000    280.000000       2.563400   
50%        435.000000   1166.000000    409.000000       3.534800   
75%        647.000000   1725.000000    605.000000       4.743250   
max       6445.000000  35682.000000   6082.000000      15.000100   

       median_house_value  
count        20640.000000  
mean        206855.816909  
std         115395.615874  
min          14999.000000  
25%         119600.000000  
50%         179700.000000  
75%         264725.000000  
max         500001.000000

In [4]:
df.info() #  showing information about datatypes

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20640 entries, 0 to 20639
Data columns (total 10 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   longitude           20640 non-null  float64
 1   latitude            20640 non-null  float64
 2   housing_median_age  20640 non-null  float64
 3   total_rooms         20640 non-null  float64
 4   total_bedrooms      20433 non-null  float64
 5   population          20640 non-null  float64
 6   households          20640 non-null  float64
 7   median_income       20640 non-null  float64
 8   median_house_value  20640 non-null  float64
 9   ocean_proximity     20640 non-null  object 
dtypes: float64(9), object(1)
memory usage: 1.6+ MB


NULL VALUES

In [5]:
df.isnull().sum() #  null values for all features

longitude               0
latitude                0
housing_median_age      0
total_rooms             0
total_bedrooms        207
population              0
households              0
median_income           0
median_house_value      0
ocean_proximity         0
dtype: int64

## Housing distribution on the map

In [6]:
plt.figure(figsize=(16,6))
fig = sns.scatterplot(df.longitude, df.latitude, hue=df['median_house_value'],
                      legend=False, palette='winter');

Houses prices increases as well as ocean distance decreases - it's not big suprise. Houses with view on the ocean are mostly more expensive.

## 2. Data Imputation

*  there's only 207 null values in total_bedrooms
*  unsupervised learning approach - KNN (K-nst Nearest Neighbours) is gonna be useful to inpute data to dataframe

In [7]:
from sklearn.neighbors import KNeighborsRegressor


def input_knn(data_frame=df):
    
    """arguments: data_frame:pandas data frame - df default
         returns: data_frame with filled Nan values"""
    
    numeric_features = df.select_dtypes(include=[np.number]) #  only features with numeric values
    caterogical_features = df.select_dtypes(exclude=[np.number])  #  only features without numeric values
    nan_columns = numeric_features.columns[numeric_features.isna().any()].to_list() #  features with empty values (NaNs)
    no_nan_columns = numeric_features.columns.difference(nan_columns).values  #  features withouy empty values
    
    
    for column in nan_columns:
        imp_test = numeric_features[numeric_features[column].isna()] #  columns with null values 
        imp_train = numeric_features.dropna()
        model = KNeighborsRegressor(n_neighbors=5)
        knr = model.fit(imp_train[no_nan_columns], imp_train[column]) #  train model takes values from columns without null values
        numeric_features.loc[df[column].isna(), column] = knr.predict(imp_test[no_nan_columns]) #  KNR predicts replaces null values
        
    return pd.concat([numeric_features, caterogical_features], axis=1)

In [8]:
df_copy = df #  even if we have new df inputed with function above it's good practice to save old data frame
df=input_knn('total_bedrooms') #  imputing data
df.describe()

longitude      latitude  housing_median_age   total_rooms  \
count  20640.000000  20640.000000        20640.000000  20640.000000   
mean    -119.569704     35.631861           28.639486   2635.763081   
std        2.003532      2.135952           12.585558   2181.615252   
min     -124.350000     32.540000            1.000000      2.000000   
25%     -121.800000     33.930000           18.000000   1447.750000   
50%     -118.490000     34.260000           29.000000   2127.000000   
75%     -118.010000     37.710000           37.000000   3148.000000   
max     -114.310000     41.950000           52.000000  39320.000000   

       total_bedrooms    population    households  median_income  \
count    20640.000000  20640.000000  20640.000000   20640.000000   
mean       537.573663   1425.476744    499.539680       3.870671   
std        420.411735   1132.462122    382.329753       1.899822   
min          1.000000      3.000000      1.000000       0.499900   
25%        296.000000    787.000000    280.000000       2.563400   
50%        435.000000   1166.000000    409.000000       3.534800   
75%        647.000000   1725.000000    605.000000       4.743250   
max       6445.000000  35682.000000   6082.000000      15.000100   

       median_house_value  
count        20640.000000  
mean        206855.816909  
std         115395.615874  
min          14999.000000  
25%         119600.000000  
50%         179700.000000  
75%         264725.000000  
max         500001.000000

## 3. EDA

### 3.1 HISTOGRAMS

I'm going to inspect columns using **univeriate analysis** (analysis of only 1 variable). Histogram is good approach in this case. It allow us to see:

* data distribution
* otuliners
* odd patterns
* scale of axis

In [9]:
def plot_histogram(column_name, data_frame=df):
    
    """arguments: column_name:str - name of the column to be ploted
       returns: histogram object
    """
    
    #  in case when column is not in data frame
    if column_name not in data_frame.columns:
        raise ValueError(f'Chose correct column from data frame colums: {data_frame.columns}')
        
    fig = px.histogram(data_frame=data_frame.sort_values(by=column_name), x=column_name,
                       color_discrete_sequence=['blue'])
    
    
    fig.update_layout(font=dict(family='Lato', size=16), 
                      title=dict(text=f'<b>histogram - {column_name}<b>',
                                font=dict(size=24),
                                x=.5),
                     plot_bgcolor='lightblue',
                     paper_bgcolor='lightblue',
                     xaxis=dict(showgrid=False),
                     yaxis=dict(showgrid=False))
    
    fig.show()

In [10]:
numeric_columns = df.select_dtypes(np.number)
for column in numeric_columns:
    plot_histogram(column)

### Odd patterns and oustliners

At first glance:
* there's outliners at housing median age and median house value. It may be due to the way in which the data was sampled (median)
* housing median age has outliner at 52k, median house value at 500k

Less noticible:
* total rooms column cointans outliners. There's big part of houses distributed between 0 - 5k but there's some houses which have even 30k and more
* total bedrooms column contains otuliners. Mots of houses distributed in between 0 and 5k.
* pupulation and household contains outliners as well. Population is distributet mostly between 0 and 5k and household 0 and 1k

Dropping outliners from population column

In [11]:
df.sort_values(by='population', ascending=False)

longitude  latitude  housing_median_age  total_rooms  total_bedrooms  \
15360    -117.42     33.35                14.0      25135.0          4819.0   
9880     -121.79     36.64                11.0      32627.0          6445.0   
13139    -121.44     38.43                 3.0      39320.0          6210.0   
10309    -117.74     33.89                 4.0      37937.0          5471.0   
6057     -117.78     34.03                 8.0      32054.0          5290.0   
...          ...       ...                 ...          ...             ...   
18210    -122.06     37.39                26.0         18.0             4.0   
12286    -116.95     33.86                 1.0          6.0             2.0   
3126     -117.79     35.21                 4.0          2.0             2.0   
12458    -114.62     33.62                26.0         18.0             3.0   
5342     -118.44     34.04                16.0         18.0             6.0   

       population  households  median_income  median_house_value  \
15360     35682.0      4769.0         2.5729            134400.0   
9880      28566.0      6082.0         2.3087            118800.0   
13139     16305.0      5358.0         4.9516            153700.0   
10309     16122.0      5189.0         7.4947            366300.0   
6057      15507.0      5050.0         6.0191            253900.0   
...           ...         ...            ...                 ...   
18210         8.0         4.0         3.7500            375000.0   
12286         8.0         2.0         1.6250             55000.0   
3126          6.0         2.0         2.3750            137500.0   
12458         5.0         3.0         0.5360            275000.0   
5342          3.0         4.0         0.5360            350000.0   

      ocean_proximity  
15360       <1H OCEAN  
9880        <1H OCEAN  
13139          INLAND  
10309       <1H OCEAN  
6057        <1H OCEAN  
...               ...  
18210        NEAR BAY  
12286          INLAND  
3126           INLAND  
12458          INLAND  
5342        <1H OCEAN  

[20640 rows x 10 columns]

In [12]:
df = df.drop(labels = [15360, 9880])
plot_histogram('population')
df.sort_values(by='population', ascending=False)

longitude  latitude  housing_median_age  total_rooms  total_bedrooms  \
13139    -121.44     38.43                 3.0      39320.0          6210.0   
10309    -117.74     33.89                 4.0      37937.0          5471.0   
6057     -117.78     34.03                 8.0      32054.0          5290.0   
6066     -117.87     34.04                 7.0      27700.0          4179.0   
12215    -117.12     33.52                 4.0      30401.0          4957.0   
...          ...       ...                 ...          ...             ...   
18210    -122.06     37.39                26.0         18.0             4.0   
12286    -116.95     33.86                 1.0          6.0             2.0   
3126     -117.79     35.21                 4.0          2.0             2.0   
12458    -114.62     33.62                26.0         18.0             3.0   
5342     -118.44     34.04                16.0         18.0             6.0   

       population  households  median_income  median_house_value  \
13139     16305.0      5358.0         4.9516            153700.0   
10309     16122.0      5189.0         7.4947            366300.0   
6057      15507.0      5050.0         6.0191            253900.0   
6066      15037.0      4072.0         6.6288            339700.0   
12215     13251.0      4339.0         4.5841            212300.0   
...           ...         ...            ...                 ...   
18210         8.0         4.0         3.7500            375000.0   
12286         8.0         2.0         1.6250             55000.0   
3126          6.0         2.0         2.3750            137500.0   
12458         5.0         3.0         0.5360            275000.0   
5342          3.0         4.0         0.5360            350000.0   

      ocean_proximity  
13139          INLAND  
10309       <1H OCEAN  
6057        <1H OCEAN  
6066        <1H OCEAN  
12215       <1H OCEAN  
...               ...  
18210        NEAR BAY  
12286          INLAND  
3126           INLAND  
12458          INLAND  
5342        <1H OCEAN  

[20638 rows x 10 columns]

### Correlation

In [13]:
df.corr().style.background_gradient()

In [14]:
def correlation_heatmap(data_frame=df):
    """arguments: data_frame:pandas DataFrame
       returns: correlation heatmap"""
    
    #  setting the context
    sns.set(context='paper', font='moonspace')
    
    #  making correlation object and saving it into variable
    correlation = df.corr()
    
    #  creating heatmap figure object (paper) and ax object (the plot)
    fig, ax = plt.subplots(figsize=(12, 8))
    
    #  generating color palettes
    cmap = sns.diverging_palette(220, 10, center='light', as_cmap=True)
    
    #  draw the heatmap
    heatmap = sns.heatmap(correlation, vmax=1,vmin=-1,center=0, square=False, annot=True, cmap=cmap,
                         lw=2, cbar=False)
    
    return heatmap

In [15]:
correlation_heatmap();

*  target variable median_house_value is quite strong correlated to median_income variable
* there's no more strong correlations - we could consider dropping some features which are very weak correlated but in this case they will stay

## 4.Training Model

### 4.1 Linear Regression

In [16]:
from sklearn.model_selection import train_test_split

X = df.drop(['median_house_value', 'ocean_proximity'], axis=1)
y = df['median_house_value']

X_train, X_test, y_train, y_test = train_test_split(X,y, test_size=.33,
                                                   random_state=42)
#  splitting the data into train and test

In [17]:
from sklearn.linear_model import LinearRegression

reg = LinearRegression() #  importing LinearRegression

reg.fit(X_train, y_train) #  fitting the train data frame and train feature to the LinearRegression

LinearRegression()

In [18]:
predictions=reg.predict(X_test)

Actual mean and predicted mean

In [19]:
print(f'actual: {y_test.mean()}')
print(f'predictions: {predictions.mean()}')

actual: 207247.0158567024
predictions: 206237.0129757717


In [20]:
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score

print('MAE: ' + str(mean_absolute_error(y_test, predictions)))
print('MSE: ' + str(mean_squared_error(y_test, predictions)))
print('Score: '+ str(r2_score(y_test, predictions)))

MAE: 50885.200510757844
MSE: 4818789918.122185
Score: 0.6462874211828635


### 4.2 Random Forest

In [21]:
from sklearn.ensemble import RandomForestRegressor
reg = RandomForestRegressor() #  importing RandomForestRegressor

In [22]:
reg.fit(X_train, y_train) #  fitting train data and train feature

RandomForestRegressor()

In [23]:
actual = y_test
predictions = reg.predict(X_test)
print(f'Actual mean: {np.mean(actual)}')
print(f'Predicted mean: {np.mean(predictions)}')

Actual mean: 207247.0158567024
Predicted mean: 207736.91371311116


In [24]:
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
print('MAE: ' + str(mean_absolute_error(y_test, predictions)))
print('MSE: ' + str(mean_squared_error(y_test, predictions)))
print('Score: '+ str(r2_score(y_test, predictions)))

MAE: 32706.12875935986
MSE: 2514774027.190158
Score: 0.8154085939802881


## 5.Conclusions

Looks like RandomForestRegressor is the winner with score: 81